# Notebook for reading in MRMS MESH data in grib format

### Import necessary libraries (xarray, cfgrib)

In [1]:
import xarray as xr
import cfgrib
import warnings
warnings.filterwarnings("ignore")
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec
import cartopy.crs as ccrs
import cartopy.feature as cfeature
import cartopy.io.shapereader as shpreader
import dask.array as da
from dask import delayed
import dask.dataframe as dd
from dask.distributed import Client
client = Client()

2022-11-14 18:24:04,001 - distributed.diskutils - INFO - Found stale lock file and directory '/tmp/dask-worker-space/worker-swb1bnyp', purging


In [2]:
client

<Client: 'tcp://127.0.0.1:34042' processes=8 threads=64, memory=755.66 GiB>

## Open all files with .grib2 extension stored in /home/scratch/mesh

In [3]:
mesh_hist = xr.open_mfdataset('/home/scratch/mesh/*.grib2', engine = 'cfgrib', parallel=True) #Make sure to include engine = cfgrib since we are working with grib2 files
#and parallel = True to run using dask

Can't create file '/home/scratch/mesh/2020.grib2.923a8.idx'
Traceback (most recent call last):
  File "/anaconda3/envs/pyEAE/lib/python3.9/site-packages/cfgrib/messages.py", line 522, in from_indexpath_or_filestream
    with compat_create_exclusive(indexpath) as new_index_file:
  File "/anaconda3/envs/pyEAE/lib/python3.9/contextlib.py", line 119, in __enter__
    return next(self.gen)
  File "/anaconda3/envs/pyEAE/lib/python3.9/site-packages/cfgrib/messages.py", line 488, in compat_create_exclusive
    fd = os.open(path, os.O_WRONLY | os.O_CREAT | os.O_EXCL)
PermissionError: [Errno 13] Permission denied: '/home/scratch/mesh/2020.grib2.923a8.idx'
Can't read index file '/home/scratch/mesh/2020.grib2.923a8.idx'
Traceback (most recent call last):
  File "/anaconda3/envs/pyEAE/lib/python3.9/site-packages/cfgrib/messages.py", line 532, in from_indexpath_or_filestream
    index_mtime = os.path.getmtime(indexpath)
  File "/anaconda3/envs/pyEAE/lib/python3.9/genericpath.py", line 55, in getmtim

In [4]:
mesh_hist #Print out dataset

<xarray.Dataset>
Dimensions:         (time: 56794, latitude: 3500, longitude: 7000)
Coordinates:
  * time            (time) datetime64[ns] 2015-05-20T00:06:00 ... 2021-12-31T...
    step            timedelta64[ns] 00:00:00
    heightAboveSea  float64 500.0
  * latitude        (latitude) float64 54.99 54.98 54.98 ... 20.03 20.02 20.01
  * longitude       (longitude) float64 230.0 230.0 230.0 ... 300.0 300.0 300.0
    valid_time      (time) datetime64[ns] dask.array<chunksize=(5208,), meta=np.ndarray>
Data variables:
    unknown         (time, latitude, longitude) float32 dask.array<chunksize=(5208, 3500, 7000), meta=np.ndarray>
Attributes:
    GRIB_edition:            2
    GRIB_centre:             161
    GRIB_centreDescription:  161
    GRIB_subCentre:          0
    Conventions:             CF-1.7
    institution:             161
    history:                 2022-11-14T18:24 GRIB to CDM+CF via cfgrib-0.9.1...

## Resample MESH data

### NOTE: will have to be saved in small chunks, i.e., not daily max. Dataset is huge, so cannot save in large subsets. Seasonal, yearly, or monthly max should work

In [5]:
mesh_yearly_max = mesh_hist.groupby('time.year').max(dim = 'time') #Use xarray's groupby function to group time dimension by yearly max (can change to min, mean, 
#median, and stdev)

In [6]:
mesh_yearly_max #Returns 7 years

<xarray.Dataset>
Dimensions:         (latitude: 3500, longitude: 7000, year: 7)
Coordinates:
    step            timedelta64[ns] 00:00:00
    heightAboveSea  float64 500.0
  * latitude        (latitude) float64 54.99 54.98 54.98 ... 20.03 20.02 20.01
  * longitude       (longitude) float64 230.0 230.0 230.0 ... 300.0 300.0 300.0
  * year            (year) int64 2015 2016 2017 2018 2019 2020 2021
Data variables:
    unknown         (year, latitude, longitude) float32 dask.array<chunksize=(1, 3500, 7000), meta=np.ndarray>

#### Select mesh variable (in this case, 'unknown')

In [7]:
mesh_yearly_max = mesh_yearly_max.unknown

In [8]:
mesh_yearly_max

<xarray.DataArray 'unknown' (year: 7, latitude: 3500, longitude: 7000)>
dask.array<concatenate, shape=(7, 3500, 7000), dtype=float32, chunksize=(1, 3500, 7000), chunktype=numpy.ndarray>
Coordinates:
    step            timedelta64[ns] 00:00:00
    heightAboveSea  float64 500.0
  * latitude        (latitude) float64 54.99 54.98 54.98 ... 20.03 20.02 20.01
  * longitude       (longitude) float64 230.0 230.0 230.0 ... 300.0 300.0 300.0
  * year            (year) int64 2015 2016 2017 2018 2019 2020 2021

### Save yearly max to netcdf

In [10]:
#mesh_yearly_max.to_netcdf('/home/scratch/jgoodin/mesh_yearly_max.nc')

2022-11-14 18:30:38,744 - distributed.worker_memory - WARNING - Unmanaged memory use is high. This may indicate a memory leak or the memory may not be released to the OS; see https://distributed.dask.org/en/latest/worker-memory.html#memory-not-released-back-to-the-os for more information. -- Unmanaged memory: 66.19 GiB -- Worker memory limit: 94.46 GiB
2022-11-14 18:30:38,843 - distributed.worker_memory - WARNING - Unmanaged memory use is high. This may indicate a memory leak or the memory may not be released to the OS; see https://distributed.dask.org/en/latest/worker-memory.html#memory-not-released-back-to-the-os for more information. -- Unmanaged memory: 66.25 GiB -- Worker memory limit: 94.46 GiB
2022-11-14 18:30:38,942 - distributed.worker_memory - WARNING - Unmanaged memory use is high. This may indicate a memory leak or the memory may not be released to the OS; see https://distributed.dask.org/en/latest/worker-memory.html#memory-not-released-back-to-the-os for more information. 

In [ ]:
#mesh_daily_max = mesh_hist.resample(time = '24H', base = 12).max(dim = 'time') #Use xarray's resample method to resample to daily max values

In [ ]:
#mesh_daily_max #Test print dataset- should return ~2555 days

In [ ]:
#mesh_daily_max.unknown.shape

## Save MESH daily max dataset to netcdf

In [ ]:
mesh_daily_max.to_netcdf('/home/scratch/jgoodin/mesh_daily_max.nc')

In [ ]:
mesh_test = xr.open_dataset('/home/scratch/jgoodin/mesh_daily_max.nc')
mesh_test

### Assign lat/lon coords to variables

In [ ]:
lats = mesh_hist.latitude.values
lons = mesh_hist.longitude.values

### Assign mesh variable to plot (in this case, listed in dataset as 'unknown')

### Convert to units of inches (provided by dataset in mm)

In [ ]:
mesh_plot = mesh_hist.unknown * 0.0393701 #can change variable name, currently unknown. Change to units of inches

In [ ]:
mesh_plot.max()

### Test plot day with large hail: Walter, AL 3/19/2018

In [ ]:
#mesh_plot.sel(time = '2018-03-19T12:00:00.000000000').plot() #Select one time with large hail to test plot- Walter, AL 3/19/2018: 5.38" hail

## Plot on map of CONUS

In [ ]:
"""
fig = plt.figure(figsize= (12,8)) #Plot a figure
gs1 = gridspec.GridSpec(2, 1, width_ratios = [3], height_ratios=[1, .05], bottom=.05, top=.95, wspace=.1)
map_proj = ccrs.LambertConformal(central_longitude = -100, central_latitude = 35) #Set projection, central lat/lon
ax = plt.subplot(projection = map_proj)
#ax.set_title('Maximum diameter hail for 2005', fontsize = 22)
ax.add_feature(cfeature.LAND.with_scale('10m')) #Add land
countries_shp = shpreader.natural_earth(resolution='50m',
                                     category='cultural',
                                     name='admin_0_countries')
for country, info in zip(shpreader.Reader(countries_shp).geometries(), 
                             shpreader.Reader(countries_shp).records()):
        if info.attributes['NAME_LONG'] != 'United States':

            ax.add_geometries([country], ccrs.PlateCarree(),
                             facecolor='lightgrey', edgecolor='k', zorder=6)
ax.add_feature(cfeature.NaturalEarthFeature('physical', 'coastline', '50m', edgecolor='k', 
                                                facecolor='None'), zorder=8) 
ax.add_feature(cfeature.BORDERS.with_scale('10m')) #Add state borders
ax.add_feature(cfeature.STATES.with_scale('10m'), facecolor = 'none') #Add US states
ax.add_feature(cfeature.NaturalEarthFeature('physical', 'ocean', '50m', edgecolor='face', 
                                                facecolor='lightsteelblue'), zorder=6)
lakes_shp = shpreader.natural_earth(resolution='50m',
                                     category='physical',
                                     name='lakes')
for lake, info in zip(shpreader.Reader(lakes_shp).geometries(), 
                             shpreader.Reader(lakes_shp).records()):
        name = info.attributes['name']
        if name == 'Lake Superior' or name == 'Lake Michigan' or \
           name == 'Lake Huron' or name == 'Lake Erie' or name == 'Lake Ontario':
            
            ax.add_geometries([lake], ccrs.PlateCarree(),
                             facecolor='lightsteelblue', edgecolor='k', zorder=6)
ax.set_extent([240,287,22,50]) #Set lat/lon boundaries
lrFig = ax.pcolormesh(lons, lats, mesh_test, cmap = 'YlOrRd', transform = ccrs.PlateCarree())
#ax.text(-126, 31, 'SON', fontsize = 62, va='bottom', ha='center', rotation='vertical', transform=ccrs.PlateCarree())
#gls = ax.gridlines(draw_labels=True, dms = True, x_inline=False, y_inline=False, color="black", linestyle="dotted", zorder = 10)
#gls.top_labels=False
#gls.right_labels=False
#gls.xlabel_style = {'size': 18, 'rotation': 0}
#gls.xpadding = 12.0
#gls.ylabel_style = {'size': 18}
#plt.title("HAIL ≥ 1.57 in (END 8.5)", fontsize = 55)
ax1 = plt.subplot(gs1[1, 0])
cb = plt.colorbar(lrFig, cax = ax1, orientation = 'horizontal', extend = 'max')
#cb.set_label('Days', fontsize = 30)
cb.ax.tick_params(labelsize = 30)
plt.subplots_adjust(bottom=0.1)
#plt.savefig('/home/scratch/jgoodin/seasonal_mesh_climos/max/end8p5_4cm_SON_max.png')
"""